In [1]:
# import pandas and bokeh
import pandas as pd
from bokeh.io import output_notebook, show
from bokeh.layouts import column
from bokeh.plotting import figure, output_file, show, reset_output
from bokeh.models import SingleIntervalTicker, LinearAxis
output_notebook()

Loading BokehJS ...

In [2]:
# reading the dataset (.csv file)
maindf = pd.read_csv("./CSV_files/AirQualityIndia.csv",  encoding = "latin1")

C:\Users\arshi\Anaconda3\lib\site-packages\IPython\core\interactiveshell.py:2728: DtypeWarning: Columns (0) have mixed types. Specify dtype option on import or set low_memory=False.
  interactivity=interactivity, compiler=compiler, result=result)


In [3]:
# sample of five random rows from the dataset
maindf.sample(n=5)

stn_code sampling_date          state  location  \
86727       NaN     17/8/2006        Gujarat  Jamnagar   
209614      NaN      25-09-07    Maharashtra    Nashik   
257947      340      15-03-04      Meghalaya  Shillong   
386336      NaN     30/9/2009  Uttar Pradesh    Jhansi   
385330      NaN     30/7/2009  Uttar Pradesh      Agra   

                                         agency  \
86727                                       NaN   
209614                                      NaN   
257947  Meghalaya State Pollution Control Board   
386336                                      NaN   
385330                                      NaN   

                                      type   so2   no2   rspm    spm  \
86727               Residential and others   9.1  17.7   79.0  146.0   
209614              Residential and others  33.5  26.3   34.0   77.0   
257947  Residential, Rural and other Areas   3.3  17.9  111.0  133.0   
386336              Residential and others   7.8  26.0  124.0  267.0   
385330                     Sensitive Areas   NaN   7.1   46.0  181.0   

                  location_monitoring_station  pm2_5        date  
86727                        Fisheries Office    NaN  2006-08-17  
209614                        RTO Colony Tank    NaN  2007-09-25  
257947  State Tuberculosis Hospital, Shillong    NaN  2004-03-15  
386336                          Jail Chauraha    NaN  2009-09-30  
385330                              Taj Mahal    NaN  2009-07-30

In [4]:
# dimensions of the dataset
maindf.shape

(435742, 13)

In [5]:
# datatype of values in each column
maindf.dtypes

stn_code                        object
sampling_date                   object
state                           object
location                        object
agency                          object
type                            object
so2                            float64
no2                            float64
rspm                           float64
spm                            float64
location_monitoring_station     object
pm2_5                          float64
date                            object
dtype: object

In [6]:
# number of unique values in each column
for col in maindf.columns.tolist():
    print("{}: {}".format(col, maindf[col].unique().size))

stn_code: 804
sampling_date: 5486
state: 37
location: 305
agency: 65
type: 11
so2: 4198
no2: 6865
rspm: 6066
spm: 6669
location_monitoring_station: 992
pm2_5: 434
date: 5068


In [7]:
# unique values in each column and their corresponding number of occurances
for col in maindf.columns:
    print(col)
    print(maindf[col].value_counts(dropna=False))
    print("\n")

stn_code
NaN        144077
193.0        1428
519.0        1280
708.0        1273
541.0        1270
710.0        1269
SAMP         1187
132          1180
61.0         1148
106.0        1125
268          1112
263.0        1106
34           1098
711.0        1092
117          1074
76.0         1066
35           1043
596.0        1041
271          1004
339           994
118           990
301.0         954
302.0         943
264.0         929
335.0         922
322.0         902
17.0          883
464.0         856
29.0          835
131.0         830
            ...  
10002.0         9
10001.0         9
173.0           9
230.0           9
270.0           9
20001.0         8
20005.0         8
244.0           8
175.0           7
798.0           7
141             6
261.0           6
211.0           6
30004.0         5
30001.0         5
30003.0         5
5.0             4
195.0           4
191.0           3
241.0           3
213.0           3
560.0           2
53.0            2
112.0           2
2

NaN                                                                                        27491
Regional Office                                                                             6261
Paonta Sahib                                                                                1599
Head Office, Bamunimaidan, Guwahati                                                         1327
ITI Building, Gopinath Nagar, Guwahati                                                      1280
Bank of Baroda Building, Near Pimpri-Chinchwad M.C. Building                                1273
Near Pragjyotish College, Santipur, Guwahati                                                1270
MPCB Sub R.O. Udyog Bhawan, Nashik                                                          1269
Industrial Area                                                                             1165
Taj Mahal                                                                                   1134
Kottayam                      

## Tailoring the dataset according to what we need
Finding out the trend of average NO2, SO2 and SPM(Suspended Particulate Matter) level over the years (90s-2015) for each state according to the dataset 

*(all values are in micrograms per cubic meter)*

In [8]:
# drop columns which are not needed
maindf.drop(["stn_code", "agency", "location_monitoring_station", "pm2_5"], axis=1, inplace=True)

In [9]:
# We find that the only rows where 'sampling_date' is not equal to 'date' are the ones which have no data recorded. So we drop 
# those rows and one of the columns out of 'sampling_date' and 'date'
maindf.loc[maindf["sampling_date"]!=maindf["sampling_date"]]

sampling_date                        state location type  so2  no2  \
435739           NaN  andaman-and-nicobar-islands      NaN  NaN  NaN  NaN   
435740           NaN                  Lakshadweep      NaN  NaN  NaN  NaN   
435741           NaN                      Tripura      NaN  NaN  NaN  NaN   

        rspm  spm date  
435739   NaN  NaN  NaN  
435740   NaN  NaN  NaN  
435741   NaN  NaN  NaN

In [10]:
# dropping 'sampling_date' column because the date in that column is represented in different formats whereas it is not so in 
# the 'date' column.
maindf.drop("sampling_date", axis=1, inplace=True)

# rename the 'date' column as 'sampling_date'
maindf.rename(columns={"date":"sampling_date"}, inplace=True)

In [11]:
# checking the dimensions and column names after dropping and renaming the columns
print(maindf.shape)
maindf.columns.tolist()

(435742, 8)


['state', 'location', 'type', 'so2', 'no2', 'rspm', 'spm', 'sampling_date']

In [12]:
# the states for which no information is available have only one row dedicated to them. So we delete those row where the
# value_counts() function for that particular state returns 1.
for state in maindf["state"].unique().tolist():
    if(maindf["state"].value_counts()[state]==1):
        maindf.drop(maindf[maindf["state"]==state].index, inplace=True)

In [13]:
# print the number of states remaining in the dataset
len(maindf["state"].unique().tolist())

33

In [14]:
# delete all the rows where no information is available
maindf = maindf.drop(maindf[(maindf["so2"].isnull()) & (maindf["no2"].isnull()) &
                   (maindf["rspm"].isnull()) & (maindf["spm"].isnull())].index)

In [15]:
# renaming the values in the 'type' column
maindf.loc[maindf["type"]=="RIRUO","type"] = "Residential, Rural and other Areas"
maindf.loc[maindf["type"]=="Industrial Area", "type"] = "Industrial"
maindf.loc[maindf["type"]=="Industrial Areas", "type"] = "Industrial"
maindf.loc[maindf["type"]=="Sensitive Area", "type"] = "Sensitive"
maindf.loc[maindf["type"]=="Sensitive Areas", "type"] = "Sensitive"
maindf.loc[maindf["type"]=="Residential and others", "type"] = "Residential"

In [16]:
# checking if the values have been changed
maindf["type"].unique().tolist()

['Residential, Rural and other Areas',
 'Industrial',
 nan,
 'Sensitive',
 'Residential']

In [17]:
# coverting the datatype of 'sampling_date' from 'object' to 'datetime'
maindf["sampling_date"] = pd.to_datetime(maindf["sampling_date"], format="%Y/%m/%d")
print(maindf["sampling_date"].dtype)
print(maindf["sampling_date"].head())
print(maindf["sampling_date"].head().tolist())

datetime64[ns]
0   1990-02-01
1   1990-02-01
2   1990-02-01
3   1990-03-01
4   1990-03-01
Name: sampling_date, dtype: datetime64[ns]
[Timestamp('1990-02-01 00:00:00'), Timestamp('1990-02-01 00:00:00'), Timestamp('1990-02-01 00:00:00'), Timestamp('1990-03-01 00:00:00'), Timestamp('1990-03-01 00:00:00')]


In [18]:
# the last date of reporting
maindf["sampling_date"].max()

Timestamp('2015-12-31 00:00:00')

In [19]:
# the first date of reporting
maindf["sampling_date"].min()

Timestamp('1987-01-01 00:00:00')

In [20]:
# states and number of state which have data before 1990
print(maindf.loc[maindf["sampling_date"]<"1990-01-01"]["state"].unique())
print(maindf.loc[maindf["sampling_date"]<"1990-01-01"]["state"].unique().size)

['Bihar' 'Chandigarh' 'Daman & Diu' 'Delhi' 'Goa' 'Gujarat' 'Haryana'
 'Himachal Pradesh' 'Karnataka' 'Kerala' 'Madhya Pradesh' 'Maharashtra'
 'Odisha' 'Puducherry' 'Punjab' 'Rajasthan' 'Tamil Nadu' 'Uttar Pradesh'
 'West Bengal']
19


In [21]:
# states and number of state which have data between 1990 and 2000
print(maindf.loc[maindf["sampling_date"].between(left="1990-01-01", right="2000-01-01")]["state"].unique())
print(maindf.loc[maindf["sampling_date"].between(left="1990-01-01", right="2000-01-01")]["state"].unique().size)

['Andhra Pradesh' 'Assam' 'Bihar' 'Chandigarh' 'Chhattisgarh'
 'Dadra & Nagar Haveli' 'Daman & Diu' 'Delhi' 'Goa' 'Gujarat' 'Haryana'
 'Himachal Pradesh' 'Karnataka' 'Kerala' 'Madhya Pradesh' 'Maharashtra'
 'Meghalaya' 'Odisha' 'Puducherry' 'Punjab' 'Rajasthan' 'Tamil Nadu'
 'Uttar Pradesh' 'West Bengal']
24


In [22]:
# states and number of state which have data between 2010 and 2015
print(maindf.loc[maindf["sampling_date"].between(left="2010-01-01", right="2015-01-01")]["state"].unique())
print(maindf.loc[maindf["sampling_date"].between(left="2010-01-01", right="2015-01-01")]["state"].unique().size)

['Andhra Pradesh' 'Arunachal Pradesh' 'Assam' 'Bihar' 'Chandigarh'
 'Chhattisgarh' 'Dadra & Nagar Haveli' 'Daman & Diu' 'Delhi' 'Goa'
 'Gujarat' 'Haryana' 'Himachal Pradesh' 'Jammu & Kashmir' 'Jharkhand'
 'Karnataka' 'Kerala' 'Madhya Pradesh' 'Maharashtra' 'Meghalaya' 'Mizoram'
 'Nagaland' 'Odisha' 'Puducherry' 'Punjab' 'Rajasthan' 'Tamil Nadu'
 'Telangana' 'Uttar Pradesh' 'Uttarakhand' 'West Bengal']
31


In [23]:
print(maindf.loc[maindf["sampling_date"]<"2016-01-01"]["state"].unique())
print(maindf.loc[maindf["sampling_date"]<"2016-01-01"]["state"].unique().size)

['Andhra Pradesh' 'Arunachal Pradesh' 'Assam' 'Bihar' 'Chandigarh'
 'Chhattisgarh' 'Dadra & Nagar Haveli' 'Daman & Diu' 'Delhi' 'Goa'
 'Gujarat' 'Haryana' 'Himachal Pradesh' 'Jammu & Kashmir' 'Jharkhand'
 'Karnataka' 'Kerala' 'Madhya Pradesh' 'Maharashtra' 'Manipur' 'Meghalaya'
 'Mizoram' 'Nagaland' 'Odisha' 'Puducherry' 'Punjab' 'Rajasthan'
 'Tamil Nadu' 'Telangana' 'Uttar Pradesh' 'Uttarakhand' 'Uttaranchal'
 'West Bengal']
33


In [24]:
# first and last date of reporting for each state
for state in maindf["state"].unique().tolist():
    print(state + ": ")
    print(maindf[maindf["state"]==state]["sampling_date"].min())
    print(maindf[maindf["state"]==state]["sampling_date"].max())
    print("\n")

Andhra Pradesh: 
1990-02-01 00:00:00
2015-12-28 00:00:00


Arunachal Pradesh: 
2014-05-08 00:00:00
2015-12-22 00:00:00


Assam: 
1991-01-01 00:00:00
2015-12-31 00:00:00


Bihar: 
1987-01-12 00:00:00
2012-12-31 00:00:00


Chandigarh: 
1989-02-01 00:00:00
2015-12-31 00:00:00


Chhattisgarh: 
1993-10-01 00:00:00
2015-12-31 00:00:00


Dadra & Nagar Haveli: 
1992-06-01 00:00:00
2015-12-30 00:00:00


Daman & Diu: 
1989-01-01 00:00:00
2015-12-30 00:00:00


Delhi: 
1987-01-09 00:00:00
2015-12-31 00:00:00


Goa: 
1987-01-04 00:00:00
2015-12-31 00:00:00


Gujarat: 
1987-01-01 00:00:00
2015-12-31 00:00:00


Haryana: 
1987-01-06 00:00:00
2015-04-30 00:00:00


Himachal Pradesh: 
1987-01-09 00:00:00
2015-12-31 00:00:00


Jammu & Kashmir: 
2009-01-06 00:00:00
2015-12-31 00:00:00


Jharkhand: 
2004-01-09 00:00:00
2015-12-30 00:00:00


Karnataka: 
1987-01-04 00:00:00
2015-12-31 00:00:00


Kerala: 
1987-03-10 00:00:00
2015-12-31 00:00:00


Madhya Pradesh: 
1988-01-07 00:00:00
2015-12-31 00:00:00


Mahar

### df1 dataframe 
Create dataframe comprising rows with average values of so2, no2, rspm and spm at every location for each sampling date

In [25]:
df1 = maindf.groupby(by=["state", "location", "sampling_date"])["state", "location", "sampling_date", "so2", "no2", "rspm", "spm"].mean()

In [26]:
# rows and columns in the dataset
df1.shape

(304832, 4)

In [27]:
# datatype of each column
df1.dtypes

so2     float64
no2     float64
rspm    float64
spm     float64
dtype: object

In [28]:
# random sample of five records in dataframe df1
df1.sample(n=5)

so2    no2   rspm     spm
state            location sampling_date                             
Kerala           Kottayam 2007-06-28      4.50  12.70   32.0   33.00
Uttarakhand      Dehradun 2015-03-26     28.00  29.00  279.0     NaN
Tamil Nadu       Salem    2000-11-01      2.80   8.70    NaN   83.00
Madhya Pradesh   Indore   2010-02-20      9.33  14.92  139.7  231.02
Himachal Pradesh Nalagarh 2010-10-16      2.00  15.00   63.0     NaN

# Analyze data from 1990-2015
Create dataframe d2 with only relevent columns and records

df2 has the mean value of so2, no2 and spm in every state for each sampling date

In [29]:
# only so2, no2 and spm columns with records starting from 1990
df2 = df1.groupby(by=["state", "sampling_date"])["so2", "no2", "spm"].mean()

In [30]:
# first five rows of df2
df2.head()

so2        no2         spm
state          sampling_date                                 
Andhra Pradesh 1990-02-01     4.700000  17.633333         NaN
               1990-03-01     5.800000  15.966667         NaN
               1990-04-01     4.766667  16.266667         NaN
               1990-05-01     3.800000  13.750000         NaN
               1990-06-01     4.266667  15.066667  108.666667

## Average SO2 and NO2 levels in each state from 1990-2000
#### *Use 'box zoom' tool beside each plot to zoom*

In [31]:
states = df2.index.get_level_values("state").unique().tolist()
print(int(len(states)/2))

d = []

for state in states:
    
    so2conc = df2.loc[(df2.index.get_level_values("sampling_date")>"1990") &
                  (df2.index.get_level_values("sampling_date")<"2000") &
                  (df2.index.get_level_values("state")==state)]["so2"].tolist()
    
    no2conc = df2.loc[(df2.index.get_level_values("sampling_date")>"1990") &
                  (df2.index.get_level_values("sampling_date")<"2000") &
                  (df2.index.get_level_values("state")==state)]["no2"].tolist()

    dates = df2.loc[(df2.index.get_level_values("sampling_date")>"1990") &
                    (df2.index.get_level_values("sampling_date")<"2000") &
                    (df2.index.get_level_values("state")==state)].index.get_level_values("sampling_date").date.tolist()
    
    p = figure(title = "concentration (1990-2000)", x_axis_type="datetime",
               x_axis_label=("Year (" + state + ")"), y_axis_label="Concentration (microgram per cubic meter)",
               plot_width=800, plot_height=250, tools = "pan,wheel_zoom,box_zoom,reset")
    
    p.line(dates, so2conc, line_width = 1, line_color="orange", legend="so2")
    p.line(dates, no2conc, line_width = 1, legend="no2")
    d.append(p)

show(column(d))

16


## Average SO2 and NO2 levels in each state from 2000-15
#### *Use 'box zoom' tool beside each plot to zoom*

In [32]:
states = df2.index.get_level_values("state").unique().tolist()
print(int(len(states)/2))

d = []

for state in states:
    
    so2conc = df2.loc[(df2.index.get_level_values("sampling_date")>"2000") &
                  (df2.index.get_level_values("sampling_date")<"2015") &
                  (df2.index.get_level_values("state")==state)]["so2"].tolist()
    
    no2conc = df2.loc[(df2.index.get_level_values("sampling_date")>"2000") &
                  (df2.index.get_level_values("sampling_date")<"2015") &
                  (df2.index.get_level_values("state")==state)]["no2"].tolist()

    dates = df2.loc[(df2.index.get_level_values("sampling_date")>"2000") &
                    (df2.index.get_level_values("sampling_date")<"2015") &
                    (df2.index.get_level_values("state")==state)].index.get_level_values("sampling_date").date.tolist()
    
    p = figure(title = "concentration (2000-2015)", x_axis_type="datetime",
               x_axis_label=("Year (" + state + ")"), y_axis_label="Concentration (microgram per cubic meter)",
               plot_width=800, plot_height=250, tools = "pan,wheel_zoom,box_zoom,reset")
    
    p.line(dates, so2conc, line_width = 1, line_color="orange", legend="so2")
    p.line(dates, no2conc, line_width = 1, legend="no2")
    d.append(p)

show(column(d))

16


## Average SPM levels in each state from 1990-2000
#### *Use 'box zoom' tool beside each plot to zoom*

In [33]:
states = df2.index.get_level_values("state").unique().tolist()
print(int(len(states)/2))

d = []

for state in states:
    
    spm = df2.loc[(df2.index.get_level_values("sampling_date")>"1990") &
                  (df2.index.get_level_values("sampling_date")<"2000") &
                  (df2.index.get_level_values("state")==state)]["spm"].tolist()

    dates = df2.loc[(df2.index.get_level_values("sampling_date")>"1990") &
                    (df2.index.get_level_values("sampling_date")<"2000") &
                    (df2.index.get_level_values("state")==state)].index.get_level_values("sampling_date").date.tolist()
    
    #ax = fig.add_subplot(6,2,i)
    p = figure(title = "spm concentration (1990-2000)", x_axis_type="datetime",
               x_axis_label=("Year (" + state + ")"), y_axis_label="Concentration (microgram per cubic meter)",
               plot_width=800, plot_height=250, tools = "pan,wheel_zoom,box_zoom,reset")
    
    p.line(dates, spm, line_width = 1, line_color="orange")
    d.append(p)

show(column(d))

16


## Average SPM levels in each state from 2000-15
#### *Use 'box zoom' tool beside each plot to zoom*

In [34]:
states = df2.index.get_level_values("state").unique().tolist()
print(int(len(states)/2))

d = []

for state in states:
    
    spm = df2.loc[(df2.index.get_level_values("sampling_date")>"2000") &
                  (df2.index.get_level_values("sampling_date")<"2015") &
                  (df2.index.get_level_values("state")==state)]["spm"].tolist()

    dates = df2.loc[(df2.index.get_level_values("sampling_date")>"2000") &
                    (df2.index.get_level_values("sampling_date")<"2015") &
                    (df2.index.get_level_values("state")==state)].index.get_level_values("sampling_date").date.tolist()
    
    #ax = fig.add_subplot(6,2,i)
    p = figure(title = "spm concentration (2000-2015)", x_axis_type="datetime",
               x_axis_label=("Year (" + state + ")"), y_axis_label="Concentration (microgram per cubic meter)",
               plot_width=800, plot_height=250, tools = "pan,wheel_zoom,box_zoom,reset")
    
    p.line(dates, spm, line_width = 1, line_color="orange")
    d.append(p)

show(column(d))

16
